#####Libraries
***

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import csv
from scipy.stats import norm
import statsmodels.api as sm
from patsy import dmatrices #a Python library for describing statistical models and building Design Matrices using R-like formulas.
import matplotlib.pyplot as plt
%matplotlib inline
from collections import Counter
from collections import defaultdict
!pip install yfinance --upgrade --no-cache-dir
import yfinance as yf
from pandas_datareader import data as pdr
yf.pdr_override()

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 62 kB 11.7 MB/s 
  Attempting uninstall: requests
    Found existing installation: requests 2.23.0
    Uninstalling requests-2.23.0:
      Successfully uninstalled requests-2.23.0


#####Load Dataset 
***

In [2]:
#φτιάχνω τη λίστα με τα assets μου -> 50 μετοχές 
#διόρθωση : θα βγάλω τυχαία άλλες 4 μετοχές μαζί με την OGN επειδή δεν έχει το ίδιο μέγεθος με τις άλλες 
#βγάζω OGN ,WRK,HST,CE,ACN
assets= ["ABBV","AEP","AIZ","ALLE","AMAT","AMP","AMZN","AVB","AVY",   
  "AXP","BDX","BF-B","BMY","BR","CARR","CDW","CHTR","CNC",   
  "CNP","COP","CTAS","CZR","DG","DPZ","DRE","DXC","META","FTV",   
  "GOOG","GPC","HIG","JPM","KR","PG","PPL","PRU",   
  "PYPL","RE","ROL","ROST","UNH","URI","V","VRSK","XOM"]

In [3]:
#άρα πρέπει να κατεβάσουμε όλα τα adj close για όλες τις τιμές όλων των μετοχών και να κάνουμε απόλυτο ranking και σε 5 κλασεις (targets)
r=pd.DataFrame(index=pdr.get_data_yahoo(assets[0],'2021-05-29','2022-08-22')['Adj Close'].index)

[*********************100%***********************]  1 of 1 completed


In [4]:
#παίρνω τιμές για ένα χρόνο και 3 μήνες
for i in assets:
  # print('i metoxi me onoma:',i,'exei megethos',pdr.get_data_yahoo(i,'2021-01-01','2022-04-01')['Adj Close'].count())
  temp= pdr.get_data_yahoo(i,'2021-05-29','2022-08-22')['Adj Close']
  temp=temp.dropna()
  r[i]=temp.values

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********

In [5]:
#φτιάχνω ένα αντίγραφο με τις τιμές για να το έχω 
rd=pd.DataFrame(r)
rd

ABBV         AEP         AIZ        ALLE        AMAT  \
Date                                                                     
2021-06-01  106.605812   81.597748  158.413422  137.195465  136.802216   
2021-06-02  105.836273   82.125130  156.835648  136.191315  137.594055   
2021-06-03  106.605812   82.422363  159.030807  135.797531  134.990860   
2021-06-04  106.748329   82.489471  159.834396  136.673691  138.425507   
2021-06-07  107.365868   82.144295  159.295395  135.856598  137.554459   
...                ...         ...         ...         ...         ...   
2022-08-15  142.289993  104.559998  166.573883  107.199997  109.499977   
2022-08-16  142.550003  104.459999  169.531708  108.459999  108.213264   
2022-08-17  141.440002  104.330002  170.836334  108.570000  105.729614   
2022-08-18  141.289993  104.370003  171.075348  109.110001  107.993820   
2022-08-19  141.850006  104.940002  171.145065  106.449997  104.363106   

                   AMP        AMZN         AVB         AVY         AXP  ...  \
Date                                                                    ...   
2021-06-01  256.874268  160.932495  203.371307  218.499512  161.456635  ...   
2021-06-02  257.275818  161.699493  205.369476  215.377533  161.811584  ...   
2021-06-03  258.382507  159.350494  205.707352  215.249924  162.205963  ...   
2021-06-04  259.939728  160.311005  204.404175  216.300385  162.679184  ...   
2021-06-07  259.401062  159.900497  204.780655  212.471527  163.586243  ...   
...                ...         ...         ...         ...         ...  ...   
2022-08-15  286.339996  143.179993  218.380005  200.366501  165.399994  ...   
2022-08-16  289.059998  144.779999  219.240005  203.294617  165.350006  ...   
2022-08-17  288.149994  142.100006  220.220001  200.137436  163.899994  ...   
2022-08-18  291.829987  142.300003  216.520004  198.693298  164.649994  ...   
2022-08-19  284.739990  138.229996  214.979996  196.253220  162.240005  ...   

                   PRU        PYPL          RE        ROL        ROST  \
Date                                                                    
2021-06-01  102.610245  259.269989  252.285995  33.223026  120.749809   
2021-06-02  102.156334  262.170013  249.654388  33.380478  118.805557   
2021-06-03  102.345459  257.790009  249.567001  32.563683  117.322830   
2021-06-04  102.544052  263.040009  251.868454  32.662090  117.313004   
2021-06-07  102.194168  260.600006  250.334167  32.278294  117.347458   
...                ...         ...         ...        ...         ...   
2022-08-15  103.603516  101.510002  273.487122  36.900002   89.844223   
2022-08-16  103.959343  102.080002  275.634125  37.490002   92.315536   
2022-08-17  103.356422   99.419998  276.498932  37.040001   92.494904   
2022-08-18  104.196556   99.860001  280.494751  37.189999   91.677780   
2022-08-19  102.199997   96.559998  279.808899  36.540001   90.691246   

                   UNH         URI           V        VRSK        XOM  
Date                                                                   
2021-06-01  398.641083  339.450012  224.728775  169.534683  56.981377  
2021-06-02  397.788361  338.470001  227.733353  171.020279  57.433758  
2021-06-03  399.856476  336.119995  226.196365  170.178467  57.659946  
2021-06-04  397.582520  332.070007  228.209335  170.990570  57.914417  
2021-06-07  392.299622  316.019989  229.379440  166.187195  57.537437  
...                ...         ...         ...         ...        ...  
2022-08-15  542.936401  337.519989  216.419998  205.327682  92.320000  
2022-08-16  544.411743  339.309998  217.139999  204.149658  91.459999  
2022-08-17  543.295288  331.380005  214.520004  203.221191  92.199997  
2022-08-18  543.514587  323.230011  215.250000  203.590576  94.379997  
2022-08-19  546.604919  316.690002  212.820007  200.236176  94.080002  

[309 rows x 45 columns]

In [6]:
rd1= rd.pct_change().shift(-1)
rd1

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
Date                                                                     
2021-06-01 -0.007219  0.006463 -0.009960 -0.007319  0.005788  0.001563   
2021-06-02  0.007271  0.003619  0.013997 -0.002891 -0.018919  0.004302   
2021-06-03  0.001337  0.000814  0.005053  0.006452  0.025444  0.006027   
2021-06-04  0.005785 -0.004184 -0.003372 -0.005978 -0.006293 -0.002072   
2021-06-07 -0.005929 -0.031516  0.005537  0.007246 -0.022379 -0.003587   
...              ...       ...       ...       ...       ...       ...   
2022-08-15  0.001827 -0.000956  0.017757  0.011754 -0.011751  0.009499   
2022-08-16 -0.007787 -0.001244  0.007695  0.001014 -0.022951 -0.003148   
2022-08-17 -0.001061  0.000383  0.001399  0.004974  0.021415  0.012771   
2022-08-18  0.003964  0.005461  0.000408 -0.024379 -0.033620 -0.024295   
2022-08-19       NaN       NaN       NaN       NaN       NaN       NaN   

                AMZN       AVB       AVY       AXP  ...       PRU      PYPL  \
Date                                                ...                       
2021-06-01  0.004766  0.009825 -0.014288  0.002198  ... -0.004424  0.011185   
2021-06-02 -0.014527  0.001645 -0.000592  0.002437  ...  0.001851 -0.016707   
2021-06-03  0.006028 -0.006335  0.004880  0.002917  ...  0.001940  0.020365   
2021-06-04 -0.002561  0.001842 -0.017702  0.005576  ... -0.003412 -0.009276   
2021-06-07  0.020669 -0.005232  0.008548  0.003556  ... -0.000093  0.009785   
...              ...       ...       ...       ...  ...       ...       ...   
2022-08-15  0.011175  0.003938  0.014614 -0.000302  ...  0.003435  0.005615   
2022-08-16 -0.018511  0.004470 -0.015530 -0.008769  ... -0.005800 -0.026058   
2022-08-17  0.001407 -0.016801 -0.007216  0.004576  ...  0.008129  0.004426   
2022-08-18 -0.028602 -0.007113 -0.012281 -0.014637  ... -0.019161 -0.033046   
2022-08-19       NaN       NaN       NaN       NaN  ...       NaN       NaN   

                  RE       ROL      ROST       UNH       URI         V  \
Date                                                                     
2021-06-01 -0.010431  0.004739 -0.016101 -0.002139 -0.002887  0.013370   
2021-06-02 -0.000350 -0.024469 -0.012480  0.005199 -0.006943 -0.006749   
2021-06-03  0.009222  0.003022 -0.000084 -0.005687 -0.012049  0.008899   
2021-06-04 -0.006092 -0.011751  0.000294 -0.013288 -0.048333  0.005127   
2021-06-07  0.005353  0.009756  0.008807  0.003722  0.026011  0.003156   
...              ...       ...       ...       ...       ...       ...   
2022-08-15  0.007850  0.015989  0.027507  0.002717  0.005303  0.003327   
2022-08-16  0.003138 -0.012003  0.001943 -0.002051 -0.023371 -0.012066   
2022-08-17  0.014451  0.004050 -0.008834  0.000404 -0.024594  0.003403   
2022-08-18 -0.002445 -0.017478 -0.010761  0.005686 -0.020233 -0.011289   
2022-08-19       NaN       NaN       NaN       NaN       NaN       NaN   

                VRSK       XOM  
Date                            
2021-06-01  0.008763  0.007939  
2021-06-02 -0.004922  0.003938  
2021-06-03  0.004772  0.004413  
2021-06-04 -0.028091 -0.006509  
2021-06-07  0.010131  0.017690  
...              ...       ...  
2022-08-15 -0.005737 -0.009315  
2022-08-16 -0.004548  0.008091  
2022-08-17  0.001818  0.023644  
2022-08-18 -0.016476 -0.003179  
2022-08-19       NaN       NaN  

[309 rows x 45 columns]

In [7]:
#first: ranks assigned in order they appear in the array
rd2=rd1.rank(axis=1,method='first')
rd2=rd2.dropna()
rd2.astype(int)
jk=rd2.copy()
jk.astype(int)

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-06-01    10   32    5     9    31   24    30   38    3   25  ...   12   
2021-06-02    37   33   41    15     2   35     4   24   19   30  ...   27   
2021-06-03    15   13   29    34    45   30    31    4   28   20  ...   17   
2021-06-04    38   20   23    17    15   28    26   32    3   37  ...   22   
2021-06-07     8    1   28    32     2   13    44    9   33   23  ...   19   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-08-12    12   35   31    34     8    5    11   20    6   10  ...    7   
2022-08-15    17   12   43    37     1   32    36   23   40   15  ...   21   
2022-08-16    19   31   42    32     7   28     8   40   11   17  ...   21   
2022-08-17    13   16   18    32    41   39    19    2    6   31  ...   35   
2022-08-18    40   41   36     9     4   10     6   27   20   18  ...   13   

            PYPL  RE  ROL  ROST  UNH  URI   V  VRSK  XOM  
Date                                                      
2021-06-01    39   4   29     2   15   14  41    36   35  
2021-06-02     3  20    1     5   36    9  11    13   34  
2021-06-03    44  36   21    10    5    2  35    27   26  
2021-06-04    12  16    8    31    7    1  36     2   14  
2021-06-07    36  27   35    34   24   45  22    38   43  
...          ...  ..  ...   ...  ...  ...  ..   ...  ...  
2022-08-12    28  14   13    18   21   27  45    44    2  
2022-08-15    28  30   42    44   19   27  20     7    2  
2022-08-16     4  39   14    35   30    6  13    25   43  
2022-08-17    29  40   27     4   17    1  24    20   43  
2022-08-18     5  32   14    24   42   12  22    16   31  

[308 rows x 45 columns]

In [8]:
def rank_data(df1):
  for i in range(len(df1.index)):
    d=df1.loc[df1.index[i]]  #της κάθε μέρας d[1] δίνει μόνο τις τιμές 
    #print(d)
    d=d.sort_values()
    d[0:9]=1
    d[9:18]=2
    d[18:27]=3
    d[27:36]=4
    d[36:45]=5
    df1.loc[df1.index[i]]=d
    #print(df1.loc[df1.index[i]])
    #print(d)
  df1=df1.astype(int)
  return df1
r5=rd2.copy()
rd3=rank_data(r5)
rd3

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-06-01     2    4    1     1     4    3     4    5    1    3  ...    2   
2021-06-02     5    4    5     2     1    4     1    3    3    4  ...    3   
2021-06-03     2    2    4     4     5    4     4    1    4    3  ...    2   
2021-06-04     5    3    3     2     2    4     3    4    1    5  ...    3   
2021-06-07     1    1    4     4     1    2     5    1    4    3  ...    3   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-08-12     2    4    4     4     1    1     2    3    1    2  ...    1   
2022-08-15     2    2    5     5     1    4     4    3    5    2  ...    3   
2022-08-16     3    4    5     4     1    4     1    5    2    2  ...    3   
2022-08-17     2    2    2     4     5    5     3    1    1    4  ...    4   
2022-08-18     5    5    4     1     1    2     1    3    3    2  ...    2   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-06-01     5   1    4     1    2    2  5     4    4  
2021-06-02     1   3    1     1    4    1  2     2    4  
2021-06-03     5   4    3     2    1    1  4     3    3  
2021-06-04     2   2    1     4    1    1  4     1    2  
2021-06-07     4   3    4     4    3    5  3     5    5  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-08-12     4   2    2     2    3    3  5     5    1  
2022-08-15     4   4    5     5    3    3  3     1    1  
2022-08-16     1   5    2     4    4    1  2     3    5  
2022-08-17     4   5    3     1    2    1  3     3    5  
2022-08-18     1   4    2     3    5    2  3     2    4  

[308 rows x 45 columns]

#####Functions
***

In [9]:
def RPS_calculation(hist_data, submission, asset_no=44):
    # print('check')
    if hist_data.shape[0]<=asset_no:
        return np.nan    
    # print('check')
    asset_id = pd.unique(hist_data.symbol)
    
    for i in range(len(pd.unique(hist_data.date))):
        if len(hist_data[hist_data.date == pd.unique(hist_data.date)[i]])<len(asset_id):
            for asset in [x for x in asset_id if x not in hist_data[hist_data.date == pd.unique(hist_data.date)[i]].symbol.values]:
                right_price = hist_data[hist_data.symbol==asset].sort_values(by='date')
                right_price = right_price[right_price.date <= pd.unique(hist_data.date)[i]]
                right_price = right_price.price.iloc[-1]
                hist_data = hist_data.append({'date' : pd.unique(hist_data.date)[i],
                                               'symbol' : asset,
                                               'price' : right_price}, ignore_index=True)

    #Compute percentage returns
    asset_id = sorted(asset_id) 

    #Compute percentage returns
    returns = pd.DataFrame(columns = ["ID", "Return"])
    
    min_date = min(hist_data.date)
    max_date = max(hist_data.date)
    # max_date = np.max(hist_data.date)
    
    for i in range(0,len(asset_id)):
        temp = hist_data.loc[hist_data.symbol==asset_id[i]]
        
        open_price = float(temp.loc[temp.date==min_date].price)
        close_price = float(temp.loc[temp.date==max_date].price)
        
        returns = returns.append({'ID': temp.symbol.iloc[0], 
                                'Return': (close_price - open_price)/open_price}, ignore_index=True)

    #Define the relevant position of each asset
    ranking = pd.DataFrame(columns=["ID", "Position", "Return"])
    ranking.ID = list(asset_id)
    ranking.Return = returns.Return
    ranking.Position = ranking.Return.rank(method = 'min')

    #Handle Ties
    Series_per_position = pd.DataFrame(columns=["Position","Series", "Rank", "Rank1", "Rank2","Rank3", "Rank4", "Rank5"])
    Series_per_position.Position = list(pd.unique(ranking.Position.sort_values(ascending=True)))
    temp = ranking.Position.value_counts()
    temp = pd.DataFrame(zip(temp.index, temp), columns = ["Rank", "Occurencies"])
    temp = temp.sort_values(by = ["Rank"],ascending=True)
    Series_per_position.Series = list(temp.Occurencies)
    Series_per_position

    total_ranks = Series_per_position.Position.values[-1]
    for i in range(0,Series_per_position.shape[0]):
    
        start_p = Series_per_position.Position[i]
        end_p = Series_per_position.Position[i] + Series_per_position.Series[i]
        temp = pd.DataFrame(columns = ["Position","Rank", "Rank1", "Rank2", "Rank3", "Rank4","Rank5"])
        temp.Position = list(range(int(start_p),int(end_p)))

        if(temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].assign(Rank=1)
            temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].assign(Rank1=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].assign(Rank=2)
            temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].assign(Rank2=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].assign(Rank=3)
            temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].assign(Rank3=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].assign(Rank=4)
            temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].assign(Rank4=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].assign(Rank=5)
            temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].assign(Rank5=1.0)
        temp = temp.fillna(0)
        Series_per_position.iloc[i,2:Series_per_position.shape[1]] = temp.mean(axis = 0).iloc[1:temp.shape[1]]

    Series_per_position = Series_per_position.drop('Series', axis = 1)
    ranking = pd.merge(ranking,Series_per_position, on = "Position")
    ranking = ranking[["ID", "Return", "Position", "Rank", "Rank1", "Rank2", "Rank3", "Rank4", "Rank5"]]
    ranking = ranking.sort_values(["Position"])
    # print(ranking)
    #Evaluate submission
    rps_sub = []
    #for aid in list((pd.unique(ranking.ID))):
    for aid in asset_id:

        target = np.cumsum(ranking.loc[ranking.ID==aid].iloc[:,4:9].values).tolist()
        frc = np.cumsum(submission.loc[submission.ID==aid].iloc[:,1:6].values).tolist()
        rps_sub.append(np.mean([(a - b)**2 for a, b in zip(target, frc)]))
    submission["RPS"] = rps_sub
    
    output = {'RPS' : np.mean(rps_sub),
              'details' : submission}
    
    return(output)

In [10]:
#Αυτή η συνάρτηση παίρνει τα data και κάνει τη dummy μέτρηση για το διάστημα ενός χρόνου (όσο οριστεί στην ουσία το insample) για μια μετοχή
n=dict() 
def dummy(st,i,p):
  flag=False
  insample=st.iloc[p:-i]
  print('arxi',insample.head(1),'kai telos ',insample.tail(1),'mikos',len(insample))
  if(len(insample)!=220):
    print('---------------------------------------------------------------',flag)
  count=defaultdict(int)
  for word in insample.values:
    count[word]+=1
  print(word,count)
  count=sorted(count.items()) #list Η πρώτη τιμή είναι η κλάση και η δεύτερη πόσες φορές είδα τον αριθμό.
  temp=[]
  for k in range(5):
    flag=True
    for l in count:
      if(l[0]==k+1):
        temp.append(l[1]/len(insample))
        flag=False
        break
    if(flag):
      temp.append(0)
  # print(temp,count)
  data={
      'prediction':temp
  }
  forecast=pd.DataFrame(data)
  return forecast
# #για όλες τις μετοχές υπολογίζεται το counter τους
dummy(rd3['ABBV'],60,50)


arxi Date
2021-08-11    5
Name: ABBV, dtype: int64 kai telos  Date
2022-05-23    4
Name: ABBV, dtype: int64 mikos 198
--------------------------------------------------------------- False
4 defaultdict(<class 'int'>, {5: 51, 1: 30, 4: 46, 3: 39, 2: 32})


prediction
0    0.151515
1    0.161616
2    0.196970
3    0.232323
4    0.257576

In [11]:
def pred(st,p):
  pred=dict()
  for j in st:
    temp=[]
    date=[]
    for i in range(56,1,-1):
      # print(i)
      date.append(rd3[j].iloc[-i:-i+1].index.date[0])
      print(date)
      temp.append(dummy(rd3[j],i,p+(60-i))['prediction'].values)
      # pred[rd3[j].name]=temp
    #for the last day 
    date.append(rd3[j].iloc[-1:].index.date[0])
    temp.append(dummy(rd3[j],1,p+59)['prediction'].values)
    pred[rd3[j].name]=temp
  # print(date)
  pred['date']=date
  pred_final=pd.DataFrame.from_dict(pred)
  # pred_final['Date']=date
  # pred_final.set_index('Date')
  # print(pred_final)
  return pred_final
# t=pred(rd3,p)

In [12]:
def create_historical(prob):
  prob=prob.rename_axis("symbol", axis="columns")
  prob=prob.T
  prob['date']=prob.columns.date[0]
  prob.columns = ['price', 'date']
  prob=prob.reset_index()
  prob=prob[['symbol','date','price']]
  return prob

In [13]:
def RPS_data(prob_final,rd):
  RPS=pd.DataFrame()

  # RPS=RPS.drop('date',axis=1)
  # print(RPS.index[2])
  for k in prob_final.index: #for everyday of a stock->index
    prob=pd.DataFrame()
    prob1=pd.DataFrame()
    predic=pd.DataFrame()
    if(prob_final['date'][k]!=prob_final['date'].tail(1).values): #if it's not for the last day 
      #for historical data of two days 
      prob=rd.loc[(rd.index.date==prob_final['date'][k])]
      prob1=rd.loc[ (rd.index.date==prob_final['date'][k+1])]
      prob=create_historical(prob)
      prob1=create_historical(prob1)
      hist_data=prob.append(prob1)
      predic=prob_final.loc[prob_final['date']==prob_final['date'][k]] #find predictions of this day
      predic=predic.drop('date',axis=1)
      # print(predic)
      data=pd.DataFrame(index=predic.columns)
      data=data.reset_index()
      # print(data)
      data[['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=(0,0,0,0,0)
      for i in range(len(np.array_split(predic.values[0],46))-1):
        data.loc[i,['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=np.array_split(predic.values[0],46)[i][0]
      data.columns = ['ID','Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']
      # print(data)

      #now we have data->predictions and hist_data->historical data so now we can call the RPS
      rps=RPS_calculation(hist_data = hist_data , submission = data)['details']
      # print(rps) ->rps for every stock for one day 
      # print(rps['RPS'])
      tmp=pd.DataFrame(rps['RPS'].values).T
      # print(tmp.T)
      RPS=RPS.append(tmp,ignore_index=True)
      # print(RPS[RPS.index==k])

      
    else:
      #for the last day
      prob=rd.loc[(rd.index.date==prob_final['date'][k])]
      prob1=rd.loc[ (rd.index.date==rd.index.date[-1])]
      prob=create_historical(prob)
      prob1=create_historical(prob1)
      hist_data=prob.append(prob1)
      # print(hist_data)
      predic=prob_final.loc[prob_final['date']==prob_final['date'][k]] #find predictions of this day
      predic=predic.drop('date',axis=1)
      # print(predic)
      data=pd.DataFrame(index=predic.columns)
      data=data.reset_index()
      # print(data)
      data[['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=(0,0,0,0,0)
      for i in range(len(np.array_split(predic.values[0],46))-1):
        data.loc[i,['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=np.array_split(predic.values[0],46)[i][0]
      data.columns = ['ID','Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']
      # print(data)

      #now we have data->predictions and hist_data->historical data so now we can call the RPS
      rps=RPS_calculation(hist_data = hist_data , submission = data)['details']
      # print(rps) ->rps for every stock for one day 
      # print(rps['RPS'])
      tmp=pd.DataFrame(rps['RPS'].values).T
      # print(tmp.T)
      RPS=RPS.append(tmp,ignore_index=True)              
  return RPS

In [14]:
def create_RPS(prob_final,RPS):
  d=prob_final['date']
  name=prob_final.columns[:-1]
  # print(np.split(name.values,len(name)))
  # print(d.values)
  RPS['date']=d.values
  RPS=RPS.set_index('date')
  RPS.columns=assets
  return RPS

#####5 days
***

In [15]:
t_5d=pred(rd3,243)

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-08-03    3
Name: PG, dtype: int64 mikos 5
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {1: 1, 5: 1, 3: 2, 4: 1})
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), 

In [16]:
t_5d=pd.DataFrame.from_dict(t_5d)
t_5d.set_index('date')

ABBV                        AEP  \
date                                                               
2022-05-31  [0.4, 0.2, 0.0, 0.2, 0.2]  [0.4, 0.4, 0.0, 0.0, 0.2]   
2022-06-01  [0.4, 0.2, 0.2, 0.0, 0.2]  [0.4, 0.4, 0.0, 0.2, 0.0]   
2022-06-02  [0.4, 0.4, 0.2, 0.0, 0.0]  [0.6, 0.2, 0.0, 0.2, 0.0]   
2022-06-03  [0.2, 0.4, 0.2, 0.0, 0.2]  [0.4, 0.2, 0.0, 0.4, 0.0]   
2022-06-06  [0.2, 0.4, 0.2, 0.0, 0.2]  [0.2, 0.4, 0.0, 0.4, 0.0]   
2022-06-07  [0.2, 0.2, 0.2, 0.0, 0.4]  [0.2, 0.4, 0.0, 0.4, 0.0]   
2022-06-08  [0.2, 0.2, 0.0, 0.0, 0.6]  [0.2, 0.6, 0.0, 0.2, 0.0]   
2022-06-09  [0.2, 0.2, 0.0, 0.0, 0.6]  [0.0, 0.6, 0.2, 0.2, 0.0]   
2022-06-10  [0.2, 0.2, 0.0, 0.2, 0.4]  [0.0, 0.6, 0.2, 0.0, 0.2]   
2022-06-13  [0.0, 0.2, 0.0, 0.2, 0.6]  [0.2, 0.4, 0.2, 0.0, 0.2]   
2022-06-14  [0.0, 0.4, 0.0, 0.2, 0.4]  [0.4, 0.2, 0.2, 0.0, 0.2]   
2022-06-15  [0.0, 0.6, 0.0, 0.2, 0.2]  [0.4, 0.2, 0.2, 0.0, 0.2]   
2022-06-16  [0.0, 0.4, 0.0, 0.2, 0.4]  [0.4, 0.2, 0.0, 0.2, 0.2]   
2022-06-17  [0.0, 0.6, 0.0, 0.0, 0.4]  [0.6, 0.2, 0.0, 0.2, 0.0]   
2022-06-21  [0.0, 0.6, 0.0, 0.0, 0.4]  [0.4, 0.2, 0.2, 0.2, 0.0]   
2022-06-22  [0.0, 0.4, 0.0, 0.0, 0.6]  [0.2, 0.2, 0.2, 0.4, 0.0]   
2022-06-23  [0.0, 0.2, 0.2, 0.0, 0.6]  [0.2, 0.0, 0.2, 0.4, 0.2]   
2022-06-24  [0.0, 0.4, 0.2, 0.0, 0.4]  [0.4, 0.0, 0.2, 0.2, 0.2]   
2022-06-27  [0.0, 0.2, 0.2, 0.2, 0.4]  [0.2, 0.0, 0.2, 0.2, 0.4]   
2022-06-28  [0.0, 0.2, 0.2, 0.4, 0.2]  [0.2, 0.0, 0.0, 0.2, 0.6]   
2022-06-29  [0.0, 0.2, 0.2, 0.6, 0.0]  [0.2, 0.0, 0.0, 0.2, 0.6]   
2022-06-30  [0.0, 0.2, 0.2, 0.6, 0.0]  [0.2, 0.0, 0.0, 0.2, 0.6]   
2022-07-01  [0.0, 0.2, 0.2, 0.6, 0.0]  [0.0, 0.0, 0.0, 0.4, 0.6]   
2022-07-05  [0.0, 0.2, 0.2, 0.6, 0.0]  [0.2, 0.0, 0.0, 0.4, 0.4]   
2022-07-06  [0.2, 0.2, 0.2, 0.4, 0.0]  [0.2, 0.0, 0.0, 0.4, 0.4]   
2022-07-07  [0.4, 0.2, 0.2, 0.2, 0.0]  [0.4, 0.0, 0.0, 0.2, 0.4]   
2022-07-08  [0.4, 0.2, 0.0, 0.2, 0.2]  [0.4, 0.0, 0.2, 0.2, 0.2]   
2022-07-11  [0.4, 0.0, 0.0, 0.4, 0.2]  [0.4, 0.0, 0.2, 0.0, 0.4]   
2022-07-12  [0.4, 0.0, 0.2, 0.2, 0.2]  [0.2, 0.0, 0.4, 0.0, 0.4]   
2022-07-13  [0.2, 0.0, 0.4, 0.2, 0.2]  [0.2, 0.0, 0.6, 0.0, 0.2]   
2022-07-14  [0.0, 0.0, 0.6, 0.2, 0.2]  [0.0, 0.0, 0.6, 0.2, 0.2]   
2022-07-15  [0.0, 0.0, 0.6, 0.4, 0.0]  [0.2, 0.0, 0.4, 0.2, 0.2]   
2022-07-18  [0.2, 0.0, 0.6, 0.2, 0.0]  [0.4, 0.0, 0.4, 0.2, 0.0]   
2022-07-19  [0.4, 0.0, 0.4, 0.2, 0.0]  [0.6, 0.0, 0.2, 0.2, 0.0]   
2022-07-20  [0.6, 0.0, 0.2, 0.2, 0.0]  [0.8, 0.0, 0.0, 0.2, 0.0]   
2022-07-21  [0.8, 0.0, 0.0, 0.2, 0.0]  [0.8, 0.2, 0.0, 0.0, 0.0]   
2022-07-22  [0.8, 0.0, 0.0, 0.2, 0.0]  [0.6, 0.2, 0.0, 0.0, 0.2]   
2022-07-25  [0.6, 0.0, 0.0, 0.4, 0.0]  [0.4, 0.2, 0.0, 0.0, 0.4]   
2022-07-26  [0.4, 0.0, 0.0, 0.4, 0.2]  [0.2, 0.2, 0.0, 0.0, 0.6]   
2022-07-27  [0.2, 0.2, 0.0, 0.4, 0.2]  [0.2, 0.2, 0.0, 0.0, 0.6]   
2022-07-28  [0.2, 0.2, 0.0, 0.4, 0.2]  [0.2, 0.0, 0.2, 0.0, 0.6]   
2022-07-29  [0.4, 0.2, 0.0, 0.2, 0.2]  [0.2, 0.0, 0.4, 0.0, 0.4]   
2022-08-01  [0.6, 0.2, 0.0, 0.0, 0.2]  [0.2, 0.0, 0.4, 0.0, 0.4]   
2022-08-02  [0.6, 0.2, 0.0, 0.2, 0.0]  [0.2, 0.0, 0.6, 0.0, 0.2]   
2022-08-03  [0.6, 0.2, 0.0, 0.2, 0.0]  [0.0, 0.0, 0.6, 0.2, 0.2]   
2022-08-04  [0.6, 0.2, 0.0, 0.2, 0.0]  [0.0, 0.0, 0.4, 0.4, 0.2]   
2022-08-05  [0.4, 0.4, 0.0, 0.2, 0.0]  [0.0, 0.2, 0.2, 0.4, 0.2]   
2022-08-08  [0.2, 0.4, 0.0, 0.2, 0.2]  [0.0, 0.2, 0.4, 0.4, 0.0]   
2022-08-09  [0.2, 0.4, 0.2, 0.0, 0.2]  [0.0, 0.2, 0.2, 0.6, 0.0]   
2022-08-10  [0.4, 0.2, 0.2, 0.0, 0.2]  [0.0, 0.4, 0.2, 0.4, 0.0]   
2022-08-11  [0.2, 0.2, 0.2, 0.2, 0.2]  [0.0, 0.4, 0.4, 0.2, 0.0]   
2022-08-12  [0.4, 0.0, 0.2, 0.2, 0.2]  [0.0, 0.2, 0.4, 0.2, 0.2]   
2022-08-15  [0.4, 0.2, 0.2, 0.2, 0.0]  [0.0, 0.2, 0.2, 0.4, 0.2]   
2022-08-16  [0.4, 0.4, 0.0, 0.2, 0.0]  [0.0, 0.4, 0.2, 0.2, 0.2]   
2022-08-17  [0.2, 0.4, 0.2, 0.2, 0.0]  [0.0, 0.2, 0.2, 0.4, 0.2]   
2022-08-18  [0.2, 0.6, 0.2, 0.0, 0.0]  [0.0, 0.4, 0.0, 0.4, 0.2]   

                                  AIZ                       ALLE  \
date                

In [17]:
RPS_5d= RPS_data(t_5d,rd)
RPS_5d= create_RPS(t_5d,RPS_5d)
RPS_5d
print(RPS_5d.mean(axis=1).mean())

0.19177142857142865


In [30]:
#for 24 June
print(RPS_5d.iloc[16].mean())
#for 22 July
print(RPS_5d.iloc[35].mean())
#for 19 August
print(RPS_5d.iloc[-1].mean())
RPS_5d.mean(axis=1)

0.26168888888888886
0.2922666666666667
0.1784888888888889


date
2022-05-31    0.193778
2022-06-01    0.135467
2022-06-02    0.226133
2022-06-03    0.166044
2022-06-06    0.188800
2022-06-07    0.178489
2022-06-08    0.185600
2022-06-09    0.171733
2022-06-10    0.144711
2022-06-13    0.227911
2022-06-14    0.233244
2022-06-15    0.147200
2022-06-16    0.199822
2022-06-17    0.187022
2022-06-21    0.205511
2022-06-22    0.147556
2022-06-23    0.261689
2022-06-24    0.185600
2022-06-27    0.180622
2022-06-28    0.143644
2022-06-29    0.168889
2022-06-30    0.174578
2022-07-01    0.250311
2022-07-05    0.161067
2022-07-06    0.246756
2022-07-07    0.199111
2022-07-08    0.190578
2022-07-11    0.200889
2022-07-12    0.183822
2022-07-13    0.187378
2022-07-14    0.216533
2022-07-15    0.195556
2022-07-18    0.180267
2022-07-19    0.119822
2022-07-20    0.166044
2022-07-21    0.292267
2022-07-22    0.206933
2022-07-25    0.211911
2022-07-26    0.203378
2022-07-27    0.161067
2022-07-28    0.181689
2022-07-29    0.198044
2022-08-01    0.186667
2022-0

#####10 days
***

In [31]:
t_10d=pred(rd3,238)
t_10d=pd.DataFrame.from_dict(t_10d)
t_10d.set_index('date')
RPS_10d= RPS_data(t_10d,rd)
RPS_10d= create_RPS(t_10d,RPS_10d)
RPS_10d
print(RPS_10d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: PG, dtype: int64 mikos 10
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {5: 2, 4: 4, 2: 1, 1: 1, 3: 2})
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), datetime.

In [32]:
#for 24 June
print(RPS_10d.iloc[16].mean())
#for 22 July
print(RPS_10d.iloc[35].mean())
#for 19 August
print(RPS_10d.iloc[-1].mean())
RPS_10d.mean(axis=1)

0.2306666666666667
0.20595555555555561
0.16720000000000004


date
2022-05-31    0.191556
2022-06-01    0.161333
2022-06-02    0.183467
2022-06-03    0.157422
2022-06-06    0.174400
2022-06-07    0.174133
2022-06-08    0.190578
2022-06-09    0.198044
2022-06-10    0.153511
2022-06-13    0.186222
2022-06-14    0.194400
2022-06-15    0.150311
2022-06-16    0.197778
2022-06-17    0.162222
2022-06-21    0.160533
2022-06-22    0.150133
2022-06-23    0.230667
2022-06-24    0.167467
2022-06-27    0.181600
2022-06-28    0.146400
2022-06-29    0.170578
2022-06-30    0.162667
2022-07-01    0.189867
2022-07-05    0.142400
2022-07-06    0.224178
2022-07-07    0.178756
2022-07-08    0.155467
2022-07-11    0.187467
2022-07-12    0.173422
2022-07-13    0.149867
2022-07-14    0.199822
2022-07-15    0.172267
2022-07-18    0.158222
2022-07-19    0.144711
2022-07-20    0.162489
2022-07-21    0.205956
2022-07-22    0.179022
2022-07-25    0.198133
2022-07-26    0.157600
2022-07-27    0.158667
2022-07-28    0.161156
2022-07-29    0.171467
2022-08-01    0.190578
2022-0

#####15 days
***

In [33]:
t_15d=pred(rd3,233)
t_15d=pd.DataFrame.from_dict(t_15d)
t_15d.set_index('date')
RPS_15d= RPS_data(t_15d,rd)
RPS_15d= create_RPS(t_15d,RPS_15d)
RPS_15d
print(RPS_15d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: PG, dtype: int64 mikos 15
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {1: 4, 3: 3, 2: 2, 5: 2, 4: 4})
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), datetime.

In [34]:
#for 24 June
print(RPS_15d.iloc[16].mean())
#for 22 July
print(RPS_15d.iloc[35].mean())
#for 19 August
print(RPS_15d.iloc[-1].mean())
RPS_15d.mean(axis=1)

0.20183703703703704
0.1888395061728395
0.17351111111111112


date
2022-05-31    0.175447
2022-06-01    0.165886
2022-06-02    0.167704
2022-06-03    0.161896
2022-06-06    0.160790
2022-06-07    0.164622
2022-06-08    0.175723
2022-06-09    0.176119
2022-06-10    0.155852
2022-06-13    0.173867
2022-06-14    0.174736
2022-06-15    0.174104
2022-06-16    0.173037
2022-06-17    0.160119
2022-06-21    0.159289
2022-06-22    0.161699
2022-06-23    0.201837
2022-06-24    0.156168
2022-06-27    0.175486
2022-06-28    0.144790
2022-06-29    0.167151
2022-06-30    0.160988
2022-07-01    0.191644
2022-07-05    0.142262
2022-07-06    0.195635
2022-07-07    0.166874
2022-07-08    0.151309
2022-07-11    0.174933
2022-07-12    0.172010
2022-07-13    0.147398
2022-07-14    0.194370
2022-07-15    0.172128
2022-07-18    0.180346
2022-07-19    0.157393
2022-07-20    0.150479
2022-07-21    0.188840
2022-07-22    0.172286
2022-07-25    0.185719
2022-07-26    0.160474
2022-07-27    0.151348
2022-07-28    0.168138
2022-07-29    0.159605
2022-08-01    0.180148
2022-0

#####One Month (22 working days)
***

In [35]:
t_1m=pred(rd3,226)
t_1m=pd.DataFrame.from_dict(t_1m)
t_1m.set_index('date')
RPS_1m= RPS_data(t_1m,rd)
RPS_1m= create_RPS(t_1m,RPS_1m)
RPS_1m
print(RPS_1m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: PG, dtype: int64 mikos 22
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {4: 5, 2: 5, 5: 4, 3: 4, 1: 4})
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), datetime.

In [36]:
#for 24 June
print(RPS_1m.iloc[16].mean())
#for 22 July
print(RPS_1m.iloc[35].mean())
#for 19 August
print(RPS_1m.iloc[-1].mean())
RPS_1m.mean(axis=1)

0.18049586776859503
0.1709090909090909
0.16484848484848486


date
2022-05-31    0.170487
2022-06-01    0.176970
2022-06-02    0.146648
2022-06-03    0.170211
2022-06-06    0.151405
2022-06-07    0.156400
2022-06-08    0.164848
2022-06-09    0.169403
2022-06-10    0.157447
2022-06-13    0.168173
2022-06-14    0.166942
2022-06-15    0.159339
2022-06-16    0.169697
2022-06-17    0.155794
2022-06-21    0.158916
2022-06-22    0.163747
2022-06-23    0.180496
2022-06-24    0.161010
2022-06-27    0.180275
2022-06-28    0.151240
2022-06-29    0.159816
2022-06-30    0.161726
2022-07-01    0.174729
2022-07-05    0.147218
2022-07-06    0.195115
2022-07-07    0.165051
2022-07-08    0.148687
2022-07-11    0.181304
2022-07-12    0.166226
2022-07-13    0.149385
2022-07-14    0.183912
2022-07-15    0.174288
2022-07-18    0.178751
2022-07-19    0.169495
2022-07-20    0.155482
2022-07-21    0.170909
2022-07-22    0.157245
2022-07-25    0.159761
2022-07-26    0.166575
2022-07-27    0.155115
2022-07-28    0.165308
2022-07-29    0.154325
2022-08-01    0.172029
2022-0

#####Two Months(44 working days)
***

In [37]:
t_2m=pred(rd3,204)
t_2m=pd.DataFrame.from_dict(t_2m)
t_2m.set_index('date')
RPS_2m= RPS_data(t_2m,rd)
RPS_2m= create_RPS(t_2m,RPS_2m)
RPS_2m
print(RPS_2m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: PG, dtype: int64 mikos 44
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {2: 10, 3: 7, 4: 11, 5: 9, 1: 7})
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), datetim

In [38]:
#for 24 June
print(RPS_2m.iloc[16].mean())
#for 22 July
print(RPS_2m.iloc[35].mean())
#for 19 August
print(RPS_2m.iloc[-1].mean())
RPS_2m.mean(axis=1)

0.17646923783287416
0.16510101010101008
0.15724058769513316


date
2022-05-31    0.156520
2022-06-01    0.187571
2022-06-02    0.136465
2022-06-03    0.164233
2022-06-06    0.148535
2022-06-07    0.159417
2022-06-08    0.154793
2022-06-09    0.155767
2022-06-10    0.155487
2022-06-13    0.170073
2022-06-14    0.173324
2022-06-15    0.160996
2022-06-16    0.172544
2022-06-17    0.148655
2022-06-21    0.158687
2022-06-22    0.168122
2022-06-23    0.176469
2022-06-24    0.146938
2022-06-27    0.163669
2022-06-28    0.162144
2022-06-29    0.160680
2022-06-30    0.164848
2022-07-01    0.176129
2022-07-05    0.157158
2022-07-06    0.168733
2022-07-07    0.154371
2022-07-08    0.152456
2022-07-11    0.172466
2022-07-12    0.157727
2022-07-13    0.151814
2022-07-14    0.173866
2022-07-15    0.161258
2022-07-18    0.166267
2022-07-19    0.162713
2022-07-20    0.161157
2022-07-21    0.165101
2022-07-22    0.163136
2022-07-25    0.153425
2022-07-26    0.164261
2022-07-27    0.160767
2022-07-28    0.166474
2022-07-29    0.156791
2022-08-01    0.159435
2022-0

#####Three months(66 working days)
***

In [39]:
t_3m=pred(rd3,182)
t_3m=pd.DataFrame.from_dict(t_3m)
t_3m.set_index('date')
RPS_3m= RPS_data(t_3m,rd)
RPS_3m= create_RPS(t_3m,RPS_3m)
RPS_3m
print(RPS_3m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: PG, dtype: int64 mikos 66
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {1: 14, 4: 14, 5: 13, 2: 17, 3: 8})
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), datet

In [40]:
#for 24 June
print(RPS_3m.iloc[16].mean())
#for 22 July
print(RPS_3m.iloc[35].mean())
#for 19 August
print(RPS_3m.iloc[-1].mean())
RPS_3m.mean(axis=1)

0.17771451892664014
0.15855524946434035
0.15376390164268955


date
2022-05-31    0.154911
2022-06-01    0.175005
2022-06-02    0.138925
2022-06-03    0.161745
2022-06-06    0.146669
2022-06-07    0.160390
2022-06-08    0.159004
2022-06-09    0.157874
2022-06-10    0.153805
2022-06-13    0.167452
2022-06-14    0.169148
2022-06-15    0.152066
2022-06-16    0.166463
2022-06-17    0.151415
2022-06-21    0.159210
2022-06-22    0.162934
2022-06-23    0.177715
2022-06-24    0.145422
2022-06-27    0.157070
2022-06-28    0.157684
2022-06-29    0.155558
2022-06-30    0.157557
2022-07-01    0.175598
2022-07-05    0.155549
2022-07-06    0.169526
2022-07-07    0.155176
2022-07-08    0.151081
2022-07-11    0.169601
2022-07-12    0.159714
2022-07-13    0.156782
2022-07-14    0.176425
2022-07-15    0.163406
2022-07-18    0.166967
2022-07-19    0.162381
2022-07-20    0.167487
2022-07-21    0.158555
2022-07-22    0.157266
2022-07-25    0.150923
2022-07-26    0.164824
2022-07-27    0.163083
2022-07-28    0.164781
2022-07-29    0.160902
2022-08-01    0.159490
2022-0

#####Six months (132 working days)
***

In [41]:
t_6m=pred(rd3,116)
t_6m=pd.DataFrame.from_dict(t_6m)
t_6m.set_index('date')
RPS_6m= RPS_data(t_6m,rd)
RPS_6m= create_RPS(t_6m,RPS_6m)
RPS_6m
print(RPS_6m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: PG, dtype: int64 mikos 132
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {2: 30, 4: 37, 1: 26, 5: 23, 3: 16})
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), dat

In [42]:
#for 24 June
print(RPS_6m.iloc[16].mean())
#for 22 July
print(RPS_6m.iloc[35].mean())
#for 19 August
print(RPS_6m.iloc[-1].mean())
RPS_6m.mean(axis=1)

0.17187633914906641
0.15222681359044996
0.14690184675033155


date
2022-05-31    0.155925
2022-06-01    0.175544
2022-06-02    0.142135
2022-06-03    0.163610
2022-06-06    0.147169
2022-06-07    0.162251
2022-06-08    0.157511
2022-06-09    0.146761
2022-06-10    0.152050
2022-06-13    0.165014
2022-06-14    0.170651
2022-06-15    0.148593
2022-06-16    0.167438
2022-06-17    0.148572
2022-06-21    0.158808
2022-06-22    0.164146
2022-06-23    0.171876
2022-06-24    0.147364
2022-06-27    0.150745
2022-06-28    0.160849
2022-06-29    0.153355
2022-06-30    0.160942
2022-07-01    0.174952
2022-07-05    0.156252
2022-07-06    0.165826
2022-07-07    0.153388
2022-07-08    0.148201
2022-07-11    0.164105
2022-07-12    0.159695
2022-07-13    0.163055
2022-07-14    0.170341
2022-07-15    0.162608
2022-07-18    0.169838
2022-07-19    0.167514
2022-07-20    0.170838
2022-07-21    0.152227
2022-07-22    0.148859
2022-07-25    0.148953
2022-07-26    0.168396
2022-07-27    0.163903
2022-07-28    0.162054
2022-07-29    0.162834
2022-08-01    0.163481
2022-0

#####Ten months (220 working days)
***

In [43]:
t_10m=pred(rd3,28)
t_10m=pd.DataFrame.from_dict(t_10m)
t_10m.set_index('date')
RPS_10m= RPS_data(t_10m,rd)
RPS_10m= create_RPS(t_10m,RPS_10m)
RPS_10m
print(RPS_10m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16)]
arxi Date
2021-08-03    2
Name: KR, dtype: int64 kai telos  Date
2022-06-15    4
Name: KR, dtype: int64 mikos 220
4 defaultdict(<class 'int'>, {2: 36, 5: 58, 3: 32, 4: 39, 1: 55})
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17)]
arxi Date
2021-08-04 

In [45]:
#for 24 June
print(RPS_10m.iloc[16].mean())
#for 22 July
print(RPS_10m.iloc[35].mean())
#for 19 August
print(RPS_10m.iloc[-1].mean())
RPS_10m.mean(axis=1)

0.16743030303030304
0.1512001836547291
0.14695169880624429


date
2022-05-31    0.159132
2022-06-01    0.166266
2022-06-02    0.148133
2022-06-03    0.161433
2022-06-06    0.151509
2022-06-07    0.163941
2022-06-08    0.157421
2022-06-09    0.150340
2022-06-10    0.151884
2022-06-13    0.163527
2022-06-14    0.165678
2022-06-15    0.151803
2022-06-16    0.164649
2022-06-17    0.150157
2022-06-21    0.158249
2022-06-22    0.162022
2022-06-23    0.167430
2022-06-24    0.151140
2022-06-27    0.154147
2022-06-28    0.156484
2022-06-29    0.155680
2022-06-30    0.160183
2022-07-01    0.166597
2022-07-05    0.155370
2022-07-06    0.161645
2022-07-07    0.152708
2022-07-08    0.151703
2022-07-11    0.161743
2022-07-12    0.158651
2022-07-13    0.159758
2022-07-14    0.165515
2022-07-15    0.162499
2022-07-18    0.165868
2022-07-19    0.164163
2022-07-20    0.167993
2022-07-21    0.151200
2022-07-22    0.150737
2022-07-25    0.151488
2022-07-26    0.165445
2022-07-27    0.161591
2022-07-28    0.162576
2022-07-29    0.164520
2022-08-01    0.162451
2022-0

#####One year (248)
***

In [46]:
t_1y=pred(rd3,0)
t_1y=pd.DataFrame.from_dict(t_1y)
t_1y.set_index('date')
RPS_1y= RPS_data(t_1y,rd)
RPS_1y= create_RPS(t_1y,RPS_1y)
RPS_1y
print(RPS_1y.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: PG, dtype: int64 mikos 248
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {2: 53, 3: 43, 4: 66, 5: 43, 1: 43})
[datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), dat

In [47]:
#for 24 June
print(RPS_1y.iloc[16].mean())
#for 22 July
print(RPS_1y.iloc[35].mean())
#for 19 August
print(RPS_1y.iloc[-1].mean())
RPS_1y.mean(axis=1)

0.16659093536825065
0.15285755578679616
0.1494020985084981


date
2022-05-31    0.159750
2022-06-01    0.165131
2022-06-02    0.149636
2022-06-03    0.161113
2022-06-06    0.151489
2022-06-07    0.163306
2022-06-08    0.156709
2022-06-09    0.150821
2022-06-10    0.151388
2022-06-13    0.163578
2022-06-14    0.164793
2022-06-15    0.151816
2022-06-16    0.163962
2022-06-17    0.151263
2022-06-21    0.156076
2022-06-22    0.160868
2022-06-23    0.166591
2022-06-24    0.152430
2022-06-27    0.154801
2022-06-28    0.156689
2022-06-29    0.153957
2022-06-30    0.161470
2022-07-01    0.166582
2022-07-05    0.153956
2022-07-06    0.162633
2022-07-07    0.153856
2022-07-08    0.151764
2022-07-11    0.160670
2022-07-12    0.158993
2022-07-13    0.160904
2022-07-14    0.165247
2022-07-15    0.162326
2022-07-18    0.164227
2022-07-19    0.162551
2022-07-20    0.166776
2022-07-21    0.152858
2022-07-22    0.152179
2022-07-25    0.151939
2022-07-26    0.163855
2022-07-27    0.161377
2022-07-28    0.160946
2022-07-29    0.163762
2022-08-01    0.161924
2022-0

#####All the samples (add each day another rank)
***

In [48]:
#Αυτή η συνάρτηση παίρνει τα data και κάνει τη dummy μέτρηση για το διάστημα ενός χρόνου (όσο οριστεί στην ουσία το insample) για μια μετοχή
n=dict() 
def dummy2(st,i):
  flag=False
  insample=st.iloc[:-i]
  print('arxi',insample.head(1),'kai telos ',insample.tail(1),'mikos',len(insample))
  # if(len(insample)!=253):
  #   print('---------------------------------------------------------------',flag)
  count=defaultdict(int)
  for word in insample.values:
    count[word]+=1
  print(word,count)
  count=sorted(count.items()) #list Η πρώτη τιμή είναι η κλάση και η δεύτερη πόσες φορές είδα τον αριθμό.
  temp=[]
  for k in range(5):
    flag=True
    for l in count:
      if(l[0]==k+1):
        temp.append(l[1]/len(insample))
        flag=False
        break
    if(flag):
      temp.append(0)
  # print(temp,count)
  data={
      'prediction':temp
  }
  forecast=pd.DataFrame(data)
  return forecast
# #για όλες τις μετοχές υπολογίζεται το counter τους
dummy2(rd3['ABBV'],60)


arxi Date
2021-06-01    2
Name: ABBV, dtype: int64 kai telos  Date
2022-05-23    4
Name: ABBV, dtype: int64 mikos 248
4 defaultdict(<class 'int'>, {2: 45, 5: 59, 1: 38, 3: 48, 4: 58})


prediction
0    0.153226
1    0.181452
2    0.193548
3    0.233871
4    0.237903

In [49]:
def pred2(st):
  pred=dict()
  for j in st:
    temp=[]
    date=[]
    for i in range(59,1,-1):
      # print(i)
      date.append(rd3[j].iloc[-i:-i+1].index.date[0])
      print(date)
      temp.append(dummy2(rd3[j],i)['prediction'].values)
      # pred[rd3[j].name]=temp
    #for the last day 
    date.append(rd3[j].iloc[-1:].index.date[0])
    temp.append(dummy2(rd3[j],1)['prediction'].values)
    pred[rd3[j].name]=temp
  # print(date)
  pred['date']=date
  pred_final=pd.DataFrame.from_dict(pred)
  # pred_final['Date']=date
  # pred_final.set_index('Date')
  # print(pred_final)
  return pred_final


In [50]:
t_all=pred2(rd3)
t_all=pd.DataFrame.from_dict(t_all)
t_all.set_index('date')
RPS_all= RPS_data(t_all,rd)
RPS_all= create_RPS(t_all,RPS_all)
RPS_all
print(RPS_all.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
[datetime.date(2022, 5, 25), datetime.date(2022, 5, 26), datetime.date(2022, 5, 27), datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), datetime.date(2022, 7, 12), datetime.date(2022, 7, 13), datetime.date(2022, 7, 14), date

In [52]:
#for 24 June
print(RPS_all.iloc[16].mean())
#for 22 July
print(RPS_all.iloc[35].mean())
#for 19 August
print(RPS_all.iloc[-1].mean())
RPS_all.mean(axis=1)

0.15129730627744156
0.1628221913641473
0.15156183207366775


date
2022-05-25    0.161140
2022-05-26    0.161240
2022-05-27    0.162756
2022-05-31    0.159562
2022-06-01    0.164486
2022-06-02    0.149756
2022-06-03    0.161516
2022-06-06    0.151159
2022-06-07    0.162886
2022-06-08    0.156734
2022-06-09    0.151167
2022-06-10    0.151579
2022-06-13    0.163464
2022-06-14    0.164118
2022-06-15    0.152733
2022-06-16    0.163430
2022-06-17    0.151297
2022-06-21    0.156377
2022-06-22    0.160668
2022-06-23    0.164844
2022-06-24    0.153377
2022-06-27    0.156392
2022-06-28    0.156420
2022-06-29    0.154619
2022-06-30    0.161172
2022-07-01    0.164442
2022-07-05    0.154845
2022-07-06    0.162001
2022-07-07    0.153710
2022-07-08    0.153054
2022-07-11    0.161325
2022-07-12    0.158461
2022-07-13    0.159391
2022-07-14    0.165260
2022-07-15    0.162241
2022-07-18    0.162822
2022-07-19    0.161682
2022-07-20    0.164562
2022-07-21    0.153568
2022-07-22    0.153677
2022-07-25    0.153722
2022-07-26    0.162595
2022-07-27    0.161602
2022-0

In [51]:
#save the best results
RPS_all.to_excel('Q2-dummy_all.xlsx')